In [ ]:
#import library
%%capture
# dev version
!pip install https://github.com/PyThaiNLP/pythainlp/archive/dev.zip

# release version 
! pip install pythainlp

!pip install epitran
!pip install sklearn_crfsuite
!pip install tensorflow deepcut
!pip install attacut
!pip install emoji
import tweepy
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
import numpy as np
import emoji
from pythainlp.tokenize import word_tokenize
from pythainlp.corpus import thai_stopwords
import re
from wordcloud import WordCloud
import matplotlib.pyplot as plt 

In [ ]:
import pandas as pd
import numpy as np
df4 = pd.read_csv('/content/drive/MyDrive/visualize project/Twitter_Data.csv')
df4.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 253295 entries, 0 to 253294
Data columns (total 17 columns):
 #   Column                Non-Null Count   Dtype 
---  ------                --------------   ----- 
 0   post_id               253295 non-null  int64 
 1   channel               253295 non-null  object
 2   account_id            253295 non-null  int64 
 3   account_username      253295 non-null  object
 4   account_display_name  253295 non-null  object
 5   link                  253295 non-null  object
 6   created_at            253295 non-null  object
 7   message               253295 non-null  object
 8   favorite              253295 non-null  int64 
 9   retweet               253295 non-null  int64 
 10  share_on_facebook     253295 non-null  int64 
 11  engagement            253295 non-null  int64 
 12  reply                 253295 non-null  int64 
 13  positive              253295 non-null  int64 
 14  neutral               253295 non-null  int64 
 15  negative         

In [ ]:
#twitter chart 
testtime = df4[['created_at','retweet']]
time = pd.DatetimeIndex(testtime.created_at)
grouped = testtime.groupby([time.hour]).retweet.sum()
dfgrouped = grouped.to_frame()
dfgrouped.info()
defgrouped = {'time':list(range(0,24)),
              'retweet':dfgrouped['retweet']}
dfnewtime = pd.DataFrame(defgrouped)
dfnewtime


<class 'pandas.core.frame.DataFrame'>
Int64Index: 24 entries, 0 to 23
Data columns (total 1 columns):
 #   Column   Non-Null Count  Dtype
---  ------   --------------  -----
 0   retweet  24 non-null     int64
dtypes: int64(1)
memory usage: 384.0 bytes


time  retweet
created_at               
0              0  4512223
1              1  2235086
2              2  1039145
3              3   533243
4              4   293040
5              5   440355
6              6   568840
7              7  1507247
8              8  2774197
9              9  4526860
10            10  5251069
11            11  6820717
12            12  7128463
13            13  7386280
14            14  5820006
15            15  6094052
16            16  5880340
17            17  7443954
18            18  7708028
19            19  9436238
20            20  9602362
21            21  8572451
22            22  7137480
23            23  5605746

In [ ]:
#twitter bar chart 
import altair as alt

bar = alt.Chart(dfnewtime).mark_bar().encode(
    x='time:O',
    y='retweet:Q'
)
rule = alt.Chart(dfnewtime).mark_rule(color='red').encode(
    y='mean(retweet):Q'
)
(bar + rule).properties(width=600)

alt.LayerChart(...)

In [ ]:
#twitter line chart
import altair as alt
line =alt.Chart(dfnewtime).mark_line().encode(
    x='time',
    y='retweet'
).properties(width=800)
line


alt.Chart(...)

In [ ]:
#twitter explore
import pandas as pd
import numpy as np
df4 = pd.read_csv('/content/drive/MyDrive/visualize project/Twitter_Data.csv')
df4.info()

#ลองนับความยาว content ใน twitter
dfcutspace = pd.DataFrame(df4['message'])

cutspace = []
for i in range(0,len(dfcutspace['message'])):
  cutspace.append(dfcutspace['message'][i].replace(" ",""))

dfcut = pd.DataFrame({'messagecl':cutspace})

cutn = []
for i in range(0,len(dfcut['messagecl'])):
  cutn.append(dfcut['messagecl'][i].replace("\n",""))
dfcut = pd.DataFrame({'messagecl':cutn})

dftwit1 = pd.DataFrame(df4)
dftwit2 = pd.concat([dftwit1,dfcut],axis=1)

sumlen = []
for i in range(0,len(dftwit2['messagecl'])):
  sumlen.append(len(dftwit2['messagecl'][i]))
dfsumlen = pd.DataFrame({'sumlen':sumlen})
dftwit2 = pd.concat([dftwit2,dfsumlen],axis=1)
dftwit2.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 253295 entries, 0 to 253294
Data columns (total 17 columns):
 #   Column                Non-Null Count   Dtype 
---  ------                --------------   ----- 
 0   post_id               253295 non-null  int64 
 1   channel               253295 non-null  object
 2   account_id            253295 non-null  int64 
 3   account_username      253295 non-null  object
 4   account_display_name  253295 non-null  object
 5   link                  253295 non-null  object
 6   created_at            253295 non-null  object
 7   message               253295 non-null  object
 8   favorite              253295 non-null  int64 
 9   retweet               253295 non-null  int64 
 10  share_on_facebook     253295 non-null  int64 
 11  engagement            253295 non-null  int64 
 12  reply                 253295 non-null  int64 
 13  positive              253295 non-null  int64 
 14  neutral               253295 non-null  int64 
 15  negative         

post_id  ... sumlen
0  1212055894281871360  ...    225
1  1212056071449141248  ...     12
2  1212056124582744066  ...    261
3  1212056142815232000  ...     44
4  1212056217423466496  ...     12

[5 rows x 19 columns]

In [ ]:
#ลองทำ Heatmap
dftwit2['created_at'] = pd.to_datetime(dftwit2['created_at'])
dftwit2['day'] = dftwit2['created_at'].dt.day_name()
dftwit2['hours'] = dftwit2['created_at'].dt.hour
dftwit2.head()

post_id  channel          account_id  ... sumlen        day hours
0  1212055894281871360  twitter  812309012985171968  ...    225  Wednesday     0
1  1212056071449141248  twitter            66280893  ...     12  Wednesday     0
2  1212056124582744066  twitter  897506189935759360  ...    261  Wednesday     0
3  1212056142815232000  twitter          1333463166  ...     44  Wednesday     0
4  1212056217423466496  twitter            66280893  ...     12  Wednesday     0

[5 rows x 21 columns]

In [ ]:
#heatmap twitter จำนวนการ retweet ในแต่ละช่วงเวลา
daynameindex = ['Sunday', 'Monday', 'Tuesday','Wednesday',"Thursday",'Friday' ,'Saturday' ]
data2 = pd.DataFrame({'day' : dftwit2['created_at'].dt.day_name().astype('str'), 'hours' : dftwit2['created_at'].dt.hour.astype('int'), 'retweet' : dftwit2['retweet']})
hours = data2['hours'].unique()
day = list({d for d in dftwit2['day']})
dataUsing = pd.DataFrame({'day' : [], 'hours' : [], 'average' : []})

for i in day :
  for j in hours :
    new_row = {'day' : i, 'hours' : j, 'average' : float(data2[(data2['day'] == i) & (data2['hours'] == j)][['retweet']].sum())}
    dataUsing = dataUsing.append(new_row, ignore_index=True)
dataUsing['hours'] = dataUsing['hours'].astype("int")
chart = alt.Chart(dataUsing).mark_rect().encode(
    x='hours:O',
    y=alt.Y('day:O', sort = daynameindex),
    color=alt.Color('average:Q', title = "")
)
chart.properties(title = "sum of retweet")

alt.Chart(...)

In [ ]:
#prepare twitter data
twitengage = dftwit2[['engagement','sumlen']].groupby(['sumlen']).engagement.sum()
col1 = set(dftwit2['sumlen'])
twitengage1 = pd.DataFrame({'sumlen':list(col1),'engagement':twitengage})
twitengage1.iloc[0:30]

sumlen  engagement
sumlen                    
1            1        1698
2            2        5998
3            3        9946
4            4        1783
5            5        5384
6            6        4731
7            7        8585
8            8       85513
9            9        5062
10          10       10058
11          11       34271
12          12       10763
13          13       17498
14          14       55855
15          15       14549
16          16      119447
17          17       17729
18          18       42487
19          19       70796
20          20       93037
21          21       42565
22          22      136710
23          23     2245376
24          24      272155
25          25      210883
26          26      369057
27          27      281287
28          28      333196
29          29      511390
30          30      793245

In [ ]:
#line chart  จำนวนความยาวของ message ต่อ engagement
import altair as alt


line2 =alt.Chart(twitengage1).mark_line().encode(
    x=alt.X('sumlen',title = 'sum string'),
    y='engagement'
)
line2.properties(width=1200)

alt.Chart(...)

In [ ]:
#Facebook Data
import pandas as pd
import numpy as np

dffbq1 = pd.read_csv('/content/drive/MyDrive/visualize project/Facebook_Data_Q1.csv')
dffbq2 = pd.read_csv('/content/drive/MyDrive/visualize project/Facebook_Data_Q2.csv')
dffbq3 = pd.read_csv('/content/drive/MyDrive/visualize project/Facebook_Data_Q3.csv')
dffbq4 = pd.read_csv('/content/drive/MyDrive/visualize project/Facebook_Data_Q4.csv')




/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (3,23) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (23) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [ ]:
#Group all FB Data
dffb= pd.concat([dffbq1,dffbq2,dffbq3,dffbq4])
dffb.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3401521 entries, 0 to 937851
Data columns (total 27 columns):
 #   Column                Dtype 
---  ------                ----- 
 0   post_id               object
 1   channel               object
 2   account_id            int64 
 3   account_username      object
 4   account_display_name  object
 5   link                  object
 6   created_at            object
 7   message               object
 8   like                  int64 
 9   love                  int64 
 10  wow                   int64 
 11  haha                  int64 
 12  sad                   int64 
 13  angry                 int64 
 14  reaction              int64 
 15  comment               int64 
 16  share                 int64 
 17  engagement            int64 
 18  purchase_intention    int64 
 19  tag_friend            int64 
 20  positive              int64 
 21  neutral               int64 
 22  negative              int64 
 23  fan                   object
 24 

In [ ]:
#cleaning FB
null = dffbq1['category'][0]
dffb['message'] = dffb['message'].replace(null, str('(รูปภาพ/วิดีโอ)'))
dffb['message'] = dffb['message'].replace(np.nan, str('(รูปภาพ/วิดีโอ)'))
for i in dffb.columns :
  dffb[i] = dffb[i].replace(null, np.nan)
dffb['created_at']=pd.to_datetime(dffb['created_at'])
dffb.loc[(dffb['created_at'] >= '2020-02-19')& (dffb['created_at'] < '2020-02-20')].sort_values(by='share',ascending=False).head(20)

post_id   channel  ...  is_photo category
720472   783584198439393_1950387725092362  facebook  ...         0      NaN
381451   214679178554162_2830907753597945  facebook  ...         0      NaN
274426  1685775051701783_2545447489067864  facebook  ...         0      NaN
387235   217262878398976_1882545611870686  facebook  ...         0      NaN
206693  1563351190645077_2475381206108733  facebook  ...         0      NaN
615728   557825984256733_2869295469776428  facebook  ...         0      NaN
756853   893405914029096_3086027304766935  facebook  ...         0      NaN
756673   893405914029096_3085194918183507  facebook  ...         0      NaN
756806   893405914029096_3085770391459293  facebook  ...         0   travel
666067   638668092887973_2997289027025856  facebook  ...         0      NaN
288411  1700670990258816_2606654312993808  facebook  ...         0      NaN
19160     104764110354005_643088563188221  facebook  ...         0      NaN
185348  1522018888083950_2646260725659755  facebook  ...         0      NaN
714478   758976890877292_2597177813723848  facebook  ...         0      NaN
99995   1319019291511601_2848493528564162  facebook  ...         0      NaN
400707   233554666838358_1257360104457804  facebook  ...         0      NaN
125541  1401745120135407_2256999721276605  facebook  ...         0      NaN
272228  1678513078861450_2781415145237899  facebook  ...         0      NaN
187394  1526415970966495_2593860840888664  facebook  ...         0      NaN
537879   416927491692221_2967322059986072  facebook  ...         0   beauty

[20 rows x 27 columns]

In [ ]:
#Top engagement FB
fbengage = dffb[['account_display_name','like','love','wow','haha','sad','angry','reaction','comment','share','engagement','is_photo']]
fbsum = fbengage.groupby(by='account_display_name').sum()
a = fbsum.sort_values(by='engagement',ascending=False).head(20)
a = a.reset_index()
a


account_display_name       like  ...  engagement  is_photo
0                         อีจัน  182161259  ...   224411370     31103
1       สิ่งเล็กๆที่เรียกว่ารัก   95479754  ...   117486240       301
2           คาราโอเกะชั้นใต้ดิน   64628073  ...   102035954        25
3                  Drama-addict   74596427  ...   100001223      3814
4   กับข้าวกับปลาโอ Plaocooking   69274949  ...    81663726       113
5   หนูน้อยบนยอดเขาอันหนาวเหน็บ   68750047  ...    81388992       337
6                     SALE HERE   38526670  ...    66890589    108818
7         ปันโปร - Punpromotion   32085025  ...    57366224     87987
8                 หมอแล็บแพนด้า   43808069  ...    56979795      1358
9               Guy Haru Family   47308227  ...    56677355      3076
10               Lowcostcosplay   21868752  ...    53974893        60
11   ผู้หญิง Salaryman Thailand   40271607  ...    53637402      9427
12                 ใต้เตียงดารา   43167408  ...    51270080      6648
13           ข้าวจ้าว หมากวนตีน   37373162  ...    49412755       206
14                       Tagple   42495247  ...    49054320         0
15                     ขอบสหนัง   32164140  ...    43825752      1040
16                       หมูหิว   26080335  ...    37067768      2064
17           อีเจี๊ยบ เลียบด่วน   27366582  ...    34839196       610
18                 I Roam Alone   27652623  ...    32183611       299
19                  Gluta Story   22243223  ...    32136766       573

[20 rows x 12 columns]

In [ ]:
#Prepare Data for stacked bar chart
df1 = a[['account_display_name','like']]
df1 =df1.rename(columns={'account_display_name':'account_display_name','like':'engage'})
df1['type'] = str('like')
df2 = a[['account_display_name','love']]
df2 =df2.rename(columns={'account_display_name':'account_display_name','love':'engage'})
df2['type'] = str('love')
df3 = a[['account_display_name','wow']]
df3 =df3.rename(columns={'account_display_name':'account_display_name','wow':'engage'})
df3['type'] = str('wow')
df4 = a[['account_display_name','haha']]
df4 =df4.rename(columns={'account_display_name':'account_display_name','haha':'engage'})
df4['type'] = str('haha')
df5 = a[['account_display_name','sad']]
df5 =df5.rename(columns={'account_display_name':'account_display_name','sad':'engage'})
df5['type'] = str('sad')
df6 = a[['account_display_name','angry']]
df6 =df6.rename(columns={'account_display_name':'account_display_name','angry':'engage'})
df6['type'] = str('angry')
dfnew1= df1.append([df2,df3,df4,df5,df6])
dfnew2 = df2.append([df3,df4,df5,df6])
dfnew1


account_display_name     engage   type
0                         อีจัน  182161259   like
1       สิ่งเล็กๆที่เรียกว่ารัก   95479754   like
2           คาราโอเกะชั้นใต้ดิน   64628073   like
3                  Drama-addict   74596427   like
4   กับข้าวกับปลาโอ Plaocooking   69274949   like
..                          ...        ...    ...
15                     ขอบสหนัง      22639  angry
16                       หมูหิว       2034  angry
17           อีเจี๊ยบ เลียบด่วน     174980  angry
18                 I Roam Alone       9421  angry
19                  Gluta Story       2218  angry

[120 rows x 3 columns]

In [ ]:
#FB stacked bar chart (include like)
import altair as alt
from vega_datasets import data

source = dfnew1
# print(source)
alt.Chart(source).mark_bar().encode(
    x='sum(engage)',
    y=alt.Y('account_display_name:N',sort = '-x'),
    color='type'
    
).properties(width=800,height=500)

alt.Chart(...)

In [ ]:
#FB stacked bar chart (not include like)
import altair as alt
from vega_datasets import data

source = dfnew2
# print(source)
character = alt.Chart(source,title = 'Character Facebook Stacked Bar Chart ').mark_bar().encode(
    x=alt.X('sum(engage)',title='Engagement'),
    y=alt.Y('account_display_name:N',sort = '-x',title = 'Top 20 Facebook Page'),
    color='type'
    
).properties(width=600,height=500).interactive()
character.save('character Facebook_stackedchart.html')
character

alt.Chart(...)

In [ ]:
#FB stacked bar Normalized chart (not include like) 
import altair as alt
from vega_datasets import data

source = dfnew2
# print(source)
character = alt.Chart(source).mark_bar().encode(
    x=alt.X('sum(engage)',stack="normalize"),
    y=alt.Y('account_display_name:N',sort = '-x'),
    color='type'
).properties(width=800,height=500).interactive()
character.save('characterchart2.html')
character

alt.Chart(...)

In [ ]:
#prepare Data For stream chart
a = dffb
a= a[['created_at','love','wow','haha','sad','angry']]
b = a.groupby(a['created_at'].dt.date).sum()
b = b.reset_index()
b.drop(b.index[363],axis=0,inplace=True)
b.drop(b.index[90],axis=0,inplace=True)
c = b.columns.to_list()
c.remove('created_at')
c
# b.tail(5)
# b.head(5)
# b['created_at'].dt.date
# c = b.columns.to_list()
# colnames = c.remove('created_at')
newdf = pd.DataFrame()
newdf2 = pd.DataFrame()

# for j in range(6):
for i in c :
    newdf = b[['created_at',str(i)]]
    newdf = newdf.drop(columns=str(i))
    newdf['count'] = b[str(i)] 
    newdf['series'] = str(i)
    newdf2 = newdf2.append(newdf)
newdf2.sort_values(by='created_at').reset_index()
newdf2['created_at'] = pd.to_datetime(newdf2['created_at'])
newdf2 = newdf2.reset_index()
newdf2 = newdf2.drop(columns='index')
newdf2


created_at   count series
0    2020-01-01  389738   love
1    2020-01-02  405741   love
2    2020-01-03  294829   love
3    2020-01-04  378487   love
4    2020-01-05  283755   love
...         ...     ...    ...
1805 2020-12-26   17492  angry
1806 2020-12-27    8242  angry
1807 2020-12-28    7185  angry
1808 2020-12-29    7952  angry
1809 2020-12-30    6673  angry

[1810 rows x 3 columns]

In [ ]:
#stream chart reaction
import altair as alt
from vega_datasets import data

source = newdf2



alt.Chart(source).mark_area().encode(
    alt.X('monthdate(created_at):T',
        axis=alt.Axis(format='%Y', domain=False, tickSize=0)
    ),
    alt.Y('sum(count):Q', stack='center', axis=None),
    alt.Color('series:N',
        scale=alt.Scale(scheme='category20b')
    )
).properties(width=800,height=500).interactive()

alt.Chart(...)

In [ ]:
#stream chart reaction
import altair as alt
from vega_datasets import data

source = newdf2



alt.Chart(source).mark_area().encode(
    alt.X('monthdate(created_at):T',
        axis=alt.Axis(format='%m', domain=False, tickSize=0)
    ),
    alt.Y('sum(count):Q', stack='center', axis=None),
    alt.Color('series:N')
    ).properties(width=800,height=500).interactive()

alt.Chart(...)

In [ ]:
#check top reaction and top message
sadtop = newdf2[newdf2['series']=='sad']
sadtop = sadtop.sort_values(by='count',ascending=False)
sadtop.head(20)
test = dffb.loc[(dffb['created_at'] >= '2020-01-10')& (dffb['created_at'] <= '2020-01-11')]
test = test[['account_display_name','created_at','message','sad','comment','share','engagement']].sort_values(by='sad',ascending=False)
test = test.head(500)
test

account_display_name          created_at  ...  share  engagement
642578                    อีจัน 2020-01-10 00:53:17  ...  38187      353170
642612                    อีจัน 2020-01-10 12:15:00  ...  16069      203767
642636                    อีจัน 2020-01-10 17:49:18  ...   1125       69383
778013                     เมีย 2020-01-10 07:02:37  ...   2944       42647
642649                    อีจัน 2020-01-10 17:57:21  ...    839       78086
...                         ...                 ...  ...    ...         ...
235609               เด่วรู้กัน 2020-01-10 16:00:57  ...      1          33
309753                   ไปวิ่ง 2020-01-10 10:04:14  ...     10         129
13339   สิ่งเล็กๆที่เรียกว่ารัก 2020-01-10 18:00:00  ...     60         266
482385             ตุ๊ดส์review 2020-01-10 08:30:12  ...     11         627
374536                   ทาสหมา 2020-01-10 20:00:18  ...    460       10503

[500 rows x 7 columns]

In [ ]:
#prepare data for heatmap and stacked area chart
a = dffb
a= a[['created_at','love','haha','sad','angry','wow']]
b = a.groupby(a['created_at'].dt.date).sum()
b = b.reset_index()
b.drop(b.index[363],axis=0,inplace=True)
b.drop(b.index[90],axis=0,inplace=True)

c = b.columns.to_list()
c.remove('created_at')
c
# b.tail(5)
# b.head(5)
# b['created_at'].dt.date
# c = b.columns.to_list()
# colnames = c.remove('created_at')
newdf = pd.DataFrame()
newdf2 = pd.DataFrame()

# for j in range(6):
for i in c :
    newdf = b[['created_at',str(i)]]
    newdf = newdf.drop(columns=str(i))
    newdf['count'] = b[str(i)] 
    newdf['series'] = str(i)
    newdf2 = newdf2.append(newdf)
    
newdf2.sort_values(by='created_at').reset_index()
newdf2['created_at'] = pd.to_datetime(newdf2['created_at'])
newdf2['month'] = newdf2['created_at'].dt.strftime('%B')
newdf2 = newdf2.reset_index()
newdf2 = newdf2.drop(columns=['index'])  
newdf2
# newdf2.loc[(newdf2['created_at'] >= '2020-02-09')& (newdf2['created_at'] < '2020-02-10')]



created_at   count series     month
0    2020-01-01  389738   love   January
1    2020-01-02  405741   love   January
2    2020-01-03  294829   love   January
3    2020-01-04  378487   love   January
4    2020-01-05  283755   love   January
...         ...     ...    ...       ...
1805 2020-12-26   44042    wow  December
1806 2020-12-27   30467    wow  December
1807 2020-12-28   40357    wow  December
1808 2020-12-29   34088    wow  December
1809 2020-12-30   39001    wow  December

[1810 rows x 4 columns]

In [ ]:
#set top message for heatmap
from datetime import timedelta

message = {'created_at':[],'series':[],'Top_post':[],'N':[]}
for i in newdf2.index:
    a = newdf2['created_at'][i]
    b = newdf2['created_at'][i]+timedelta(days=1)
    c = newdf2['series'][i]
    test = dffb.loc[(dffb['created_at'] >= a ) & (dffb['created_at'] < b)]
    test = test[['account_display_name','created_at','message',c,'comment','share','engagement']].sort_values(by=c,ascending=False)
    d = test.iloc[:5,:]
    d = d.reset_index()
    d = d.drop(columns=['index'])   
    mess = str(d['account_display_name'][0])+':'+str(d['message'][0])+':'+str(' '+ str(d[c][0])) +str(' '+c)    
    message['created_at'].append(a)
    message['series'].append(c)
    message['Top_post'].append(mess)
    message['N'].append(d[c][0])
dfmess = pd.DataFrame.from_dict(message)
dfmess = dfmess[['Top_post','N']]
newdf3 = pd.DataFrame()
newdf3 = pd.concat([newdf2, dfmess], axis=1, join="inner")
newdf3
#test วันเกิดเหตุการณ์ไม่ปกติ
newdf3.loc[(newdf3['created_at'] >= '2020-02-09')& (newdf3['created_at'] < '2020-02-10')]


created_at  ...       N
39   2020-02-09  ...   27409
401  2020-02-09  ...   18060
763  2020-02-09  ...  113149
1125 2020-02-09  ...   11843
1487 2020-02-09  ...    1605

[5 rows x 6 columns]

In [ ]:
#Merge DataFrame for heatmap
newdf4= pd.DataFrame()
newdf5 = pd.DataFrame()
newdf5 = newdf3['Top_post']
newdf4 = newdf2.join(newdf5,how='left')
newdf4.loc[(newdf4['created_at'] >= '2020-02-09')& (newdf4['created_at'] < '2020-02-10')]

created_at  ...                                           Top_post
39   2020-02-09  ...  อีจัน:จากเหตุทหารกราดยิงผู้บริสุทธิ์ ในพื้นที่...
401  2020-02-09  ...  Bie The Ska:มาโรงเรียนสาย.. ทำไงดี!!\nมาโรงเรี...
763  2020-02-09  ...  อีจัน:หัวอกผู้ที่ต้องสูญเสีย...\n\nไม่มีคำไหนจ...
1125 2020-02-09  ...               ไข่แมวx:(รูปภาพ/วิดีโอ): 11843 angry
1487 2020-02-09  ...  กับข้าวกับปลาโอ Plaocooking:ขนมจีนน้ำเงี้ยวซุป...

[5 rows x 5 columns]

In [ ]:
#Facebook Reactions Normalized Chart 
import altair as alt
from vega_datasets import data
domain = ['angry','haha','love','sad','wow']
range_ = ['#d62728','#fdae6b', '#e377c2', '#636363',  '#6baed6']

source = newdf2

# print(source)
area1 = alt.Chart(source,title="Facebook Reactions 2020 Normalized Chart  ").mark_area().encode(
    x=alt.X("monthdate(created_at):T",title="Month-Date"),
    y=alt.Y("sum(count):Q", stack="normalize",title="Sum of Reactions"),
    color=alt.Color('series:N', scale=alt.Scale(domain=domain, range=range_),title='reactions')
).properties(width=1000,height=300).interactive()
area1

alt.Chart(...)

In [ ]:
#heatmap + tootip show toppost 
import altair as alt
from vega_datasets import data
from datetime import datetime
import calendar


source = newdf4
# source
alt.Chart(
    source,
    title="Facebook Reactions"
).mark_rect().encode(
    x='monthdate(created_at):O',
    y='series:N',
    color=alt.Color('sum(count):Q', scale=alt.Scale(scheme="yelloworangered")),
    tooltip=[
        alt.Tooltip('monthdate(created_at):T', title='Date'),
        alt.Tooltip('sum(count):Q', title='Count'),
        alt.Tooltip('Top_post:N', title='Toppost')
    ]
).interactive().properties(width=600,height=200,title="Reaction")






alt.Chart(...)

In [ ]:
#heatmap + tootip show toppost + selection time + area chart
import pandas as pd
import altair as alt
import calendar
listmonth = list(calendar.month_name)[1:13]
listmonth

base = alt.Chart(
    source,
    title="Facebook Reactions"
).mark_rect(stroke='black',strokeWidth=0.5).encode(
    x=alt.X('monthdate(created_at):T',title='Date'),
    y=alt.Y('series:N',title='Reactions'),
    color=alt.Color('sum(count):Q',scale=alt.Scale(scheme='yelloworangered'),title='Sum of reactions'),
    tooltip=[alt.Tooltip('monthdate(created_at):T',title='เดือน'), alt.Tooltip('sum(count):Q',title='Sum of reaction'),alt.Tooltip('Top_post:N')]
)
dropdown = listmonth
month_dropdown = alt.binding_select(options=dropdown)
month_select = alt.selection_single(fields=['month'], bind=month_dropdown,name="Month", init={'month': 'January'})

filter_month = base.add_selection(
    month_select
).transform_filter(
    month_select
).properties(width=800,height=200,title="Monthly Facebook Reactions ")

reactionchart = (area1) & (filter_month)
reactionchart.save('reactionchart_heatmap.html')
reactionchart





alt.VConcatChart(...)

In [ ]:
#test count word แทน top post
test = dffb.loc[(dffb['created_at'] >= '2020-02-09')& (dffb['created_at'] < '2020-02-10')]
test = test[['account_display_name','created_at','message','sad','comment','share','engagement']].sort_values(by='sad',ascending=False)
test = test.head(100)
test


account_display_name          created_at  ...  share  engagement
645878                  อีจัน 2020-02-09 15:00:07  ...  17362      353008
645919                  อีจัน 2020-02-09 21:13:35  ...   5032      139008
645846                  อีจัน 2020-02-09 11:05:40  ...   7161      154410
651560                  อีจัน 2020-02-09 17:56:25  ...   3251       69303
645833                  อีจัน 2020-02-09 01:37:49  ...   7109       54311
...                       ...                 ...  ...    ...         ...
778532                   เมีย 2020-02-09 18:42:16  ...    136        1758
268478  BigBike Thailand Club 2020-02-09 12:33:08  ...    370        3328
79042       สุดสัปดาห์แฟนคลับ 2020-02-09 20:25:31  ...     75        3607
645882                  อีจัน 2020-02-09 16:13:30  ...      5        1513
645883                  อีจัน 2020-02-09 16:13:30  ...      4        1398

[100 rows x 7 columns]

In [ ]:
#cleaning message
df = test['message']
df = df.to_frame()
def cleanText(text):
  # text = re.sub('[^ก-๙]','',text)
  stop_word = list(thai_stopwords())
  sentence = word_tokenize(text,engine="multi_cut")
  result = [word for word in sentence if word not in stop_word and " " not in word]
  return text
cleaning = []
for txt in df["message"]:
    cleaning.append(cleanText(txt))
cleaning[:10]




[nan,
 '#ชุมนุมชุลมุนขึ้นเรื่อยๆ \n\nล่าสุด 18.40 น. ตำรวจมีการประกาศสลายการการชุมนุม โดยให้เวลากับผู้ชุมนุม 3 นาที พร้อมประกาศดังลั่น “ให้ผู้ชุมนุมกลับบ้านหาพ่อเเม่ อนาคตน้องๆยังอีกยาวไกล” \nก่อนจะฉีดน้ำแรงดันสูงผสมสี ใส่ผู้ชุมนุม \n\nอย่าลืมกดติดดาว ⭐️ เพจด้วยนะ \nจะได้ไม่พลาดโพสต์ของเรา \n.................................................\nติดตามข่าวอื่นๆ ได้ใน www.ejan.co\n📌อีจันอินบ็อกซ์ เรื่องสุข ทุกข์ ร้องเรียน คลิกที่ลิงค์นี้ http://nav.cx/h9ppIoQ\n📌อีจันตลาดเเตก ซื้อ-ขายสินค้ากับเรา \nคลิกที่ลิงค์นี้ http://nav.cx/dKVukwO',
 nan,
 '#ใช้แก๊สน้ำตาสลายการชุมนุม \n\n 19.00 น. ตำรวจมีการประกาศสลายการการชุมนุม จะฉีดน้ำแรงดันสูงผสมสี ใส่ผู้ชุมนุม ซึ่งกลุ่มผู้ชุมนุมบอกว่าน้ำดังกล่าวมีฤทธิ์ทำให้เกิดอาการปวดแสบปวดร้อน \n\nก่อนที่ผู้ชุมนุมจะถอยออกมาเพื่อล้างหน้า และมีการปาแก๊สน้ำตาเพื่อพยายามสลายการชุมนุมระหว่างการฉีดน้ำ ทำให้ผู้ชุมนุมต้องถอยออกมาล้างหน้าเพราะมีอาการแสบตา \n\n19.18 มีเสียงคล้ายปะทัดดังขึ้น คาดว่าเป็นเเก๊สน้ำตา \n\nอย่าลืมกดติดดาว ⭐️ เพจด้วยนะ \nจะได้ไม่พลาดโพสต์ของเรา \n.

In [ ]:
#cleaning message
df['cleaning'] = cleaning
df

message                                           cleaning
470903                                                NaN                                                NaN
762668  #ชุมนุมชุลมุนขึ้นเรื่อยๆ \n\nล่าสุด 18.40 น. ต...  #ชุมนุมชุลมุนขึ้นเรื่อยๆ \n\nล่าสุด 18.40 น. ต...
470904                                                NaN                                                NaN
762673  #ใช้แก๊สน้ำตาสลายการชุมนุม \n\n 19.00 น. ตำรวจ...  #ใช้แก๊สน้ำตาสลายการชุมนุม \n\n 19.00 น. ตำรวจ...
762514  #นายกลั่นไม่ออกจากตำแหน่ง \n\nนายกลั่นชัด ไม่ล...  #นายกลั่นไม่ออกจากตำแหน่ง \n\nนายกลั่นชัด ไม่ล...
...                                                   ...                                                ...
762462  #ใครมาชุมนุมมีความผิด\n\nกลุ่มผู้ชุมนุมแยกราชป...  #ใครมาชุมนุมมีความผิด\n\nกลุ่มผู้ชุมนุมแยกราชป...
611995                                      ผมเท่มั้ยฮะ 😉                                      ผมเท่มั้ยฮะ 😉
762535  #ตำรวจบุกไทยซัมมิท \n\n ด่วน!!!\n\nวันนี้ 16 ต...  #ตำรวจบุกไทยซัมมิท \n\n ด่วน!!!\n\nวันนี้ 16 ต...
695711  ประเทศที่กำลังสูญสิ้นความเป็นมนุษย์ #16ตุลาไปแ...  ประเทศที่กำลังสูญสิ้นความเป็นมนุษย์ #16ตุลาไปแ...
611994                            ป ร ะ ยุ ด หั ว ค ว ย 🤬                            ป ร ะ ยุ ด หั ว ค ว ย 🤬

[100 rows x 2 columns]

In [ ]:
#cleaning message + ลบคำที่ไม่มีความหมาย
def cleanText(text):
    text = str(text)
    text = re.sub('[^ก-๙]','',text)
    stop_word = list(thai_stopwords())+['คลิก','อี','จัน','ข่าว','เพจ','ลิงค์','บาท','ร้าน']
    sentence = word_tokenize(text)
    # sentence = word_tokenize(text)
    result = [word for word in sentence if word not in stop_word and " " not in word]
    return ",".join(result)

def tokenize(d):  
    result = d.split(",")
    result = list(filter(None, result))
    return result

new_text = []
for txt in df['cleaning']:
    new_text.append(cleanText(txt))


vectorizer = CountVectorizer(tokenizer=tokenize)
transformed_data = vectorizer.fit_transform(new_text)
count_data = zip(vectorizer.get_feature_names(), np.ravel(transformed_data.sum(axis=0)))
keyword_df = pd.DataFrame(columns = ['word', 'count'])
keyword_df['word'] = vectorizer.get_feature_names()
keyword_df['count'] = np.ravel(transformed_data.sum(axis=0))   
keyword_df.sort_values(by=['count'], ascending=False).head(10)
#สรุป การเลือก top post ในวันนั้นให้ความหมายดีกว่าการนับคำ เพราะโมเดลมักนับคำที่ไม่มีความหมายมาด้วย มีบางกรณีเท่านั้นที่เห็นประเด็นขัดเจน

word  count
237   ชุมนุม    145
315    ตำรวจ     64
435      น้ำ     47
818     สลาย     42
124       คน     36
475     ปทุม     34
321   ติดตาม     32
605  พื้นที่     32
918     อย่า     31
275       ดี     30

In [ ]:
#ลองเปลี่ยน normalized stacked area เป็น Layered Area Chart 
import altair as alt
from vega_datasets import data

source = newdf2
print(source)
alt.Chart(source).mark_area(opacity=0.3).encode(
    x="monthdate(created_at):T",
    y=alt.Y("sum(count):Q", stack=None),
    color="series:N"
).interactive()

    created_at   count series
0   2020-01-01  389738   love
1   2020-01-02  405741   love
2   2020-01-03  294829   love
3   2020-01-04  378487   love
4   2020-01-05  283755   love
..         ...     ...    ...
359 2020-12-27   30467    wow
360 2020-12-28   40357    wow
361 2020-12-29   34088    wow
362 2020-12-30   39001    wow
363 2020-12-31       0    wow

[1820 rows x 3 columns]


alt.Chart(...)